In [1]:
import os
import sys
module_path = os.path.abspath(os.path.join('../../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [2]:
print(module_path)

/Users/revilooliver/Documents/quantum_computing/research/pauli_sandwitching/cut4mitigation


In [3]:
# author: Ji Liu email: ji.liu@anl.gov

import itertools, numpy
import circuit_cutter
import mlrecon_methods as ml
import numpy as np
import mthree

import qiskit
from qiskit import *
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, Aer, execute, transpile

from qiskit.transpiler import PassManager

from qiskit.converters import circuit_to_dag
from qiskit.visualization import dag_drawer, plot_histogram
from qiskit.compiler import assemble

from qiskit.tools.monitor import job_monitor, backend_monitor, backend_overview

import qiskit.providers.aer.noise as noise
from qiskit.providers.aer.noise import NoiseModel

from utils.utils import filter_results, dict_to_list, H_distance, total_counts, norm_dict
from utils.vqe_utils import read_from_file, MeasureCircuit, find_commute_groups, evaluation, apply_checking_circuit
from mlrecon_methods import run_circuits, collect_fragment_circuits

In [4]:
qiskit.__qiskit_version__

{'qiskit-terra': '0.22.2', 'qiskit-aer': '0.11.1', 'qiskit-ignis': '0.7.1', 'qiskit-ibmq-provider': '0.19.2', 'qiskit': '0.39.2', 'qiskit-nature': '0.5.1', 'qiskit-finance': None, 'qiskit-optimization': None, 'qiskit-machine-learning': None}

In [5]:
numpy.set_printoptions(linewidth = 200)

simulation_backend = "qasm_simulator"

In [6]:
IBMQ.load_account()
provider = IBMQ.get_provider(hub='ibm-q-ornl', group='ornl', project='chm185')
provider.backends()

[<IBMQSimulator('ibmq_qasm_simulator') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_montreal') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_toronto') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_kolkata') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_mumbai') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_lima') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_belem') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_quito') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_guadalupe') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_statevector') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_mps') from IBMQ(hub='ibm-q-ornl', grou

In [7]:
device = provider.get_backend('ibm_auckland')
device

<IBMQBackend('ibm_auckland') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>

In [8]:
device.configuration().to_dict()['max_shots']

100000

In [9]:
from qiskit import IBMQ, Aer
from qiskit.providers.aer.noise import NoiseModel
noise_model = NoiseModel.from_backend(device, gate_error = False, thermal_relaxation= False)
print(noise_model)

NoiseModel:
  Basis gates: ['cx', 'id', 'reset', 'rz', 'sx', 'x']
  Instructions with noise: ['measure']
  Qubits with noise: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26]
  Specific qubit errors: [('measure', (0,)), ('measure', (1,)), ('measure', (2,)), ('measure', (3,)), ('measure', (4,)), ('measure', (5,)), ('measure', (6,)), ('measure', (7,)), ('measure', (8,)), ('measure', (9,)), ('measure', (10,)), ('measure', (11,)), ('measure', (12,)), ('measure', (13,)), ('measure', (14,)), ('measure', (15,)), ('measure', (16,)), ('measure', (17,)), ('measure', (18,)), ('measure', (19,)), ('measure', (20,)), ('measure', (21,)), ('measure', (22,)), ('measure', (23,)), ('measure', (24,)), ('measure', (25,)), ('measure', (26,))]


In [10]:
noisy_simulator = provider.get_backend('ibmq_qasm_simulator')

In [11]:
front_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_front.qasm")

In [12]:
mid_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_mid.qasm")

In [13]:
end_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_end.qasm")

In [14]:
orign_circuit = front_layer + mid_layer + end_layer

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_31273/743480212.py:1: DeprecationWarning: The QuantumCircuit.__add__() method is being deprecated.Use the compose() method which is more flexible w.r.t circuit register compatibility.
  orign_circuit = front_layer + mid_layer + end_layer


In [15]:
orign_circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐           │         »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘                     »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐                      »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘                      »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐                     »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘                     »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────────────────────────»
      └────────────────┘ └────────────────┘                                   »
q_8: ─────────────────────────────────────────────────────────────────────────»
                                                                              »
«        ┌────────────┐                                                      »
«q_0: ───┤ Rz(1.5641) ├──────────────────────────────────────────────────────»
«     ┌──┴────────────┴─┐┌─────────────┐                                     »
«q_1: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘├─────────────┴┐ ┌─────────────┐                    »
«q_2: ─────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├────────────────────»
«              │         └──────────────┘┌┴─────────────┴─┐ ┌──────────────┐ »
«q_3: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├─»
«                               │        └────────────────┘┌┴──────────────┴┐»
«q_4: ──────────────────────────■────────────────■─────────┤ Ry(-8.148e-06) ├»
«                                                │         └────────────────┘»
«q_5: ───────────────────────────────────────────■─────────────────■─────────»
«                                                                  │         »
«q_6: ─────────────────────────────────────────────────────────────■─────────»
«                                                                            »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_8: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                           
«q_0: ──────────────────────────────────────────────────────
«                                                           
«q_1: ──────────────────────────────────────────────────────
«                                                           
«q_2: ──────────────────────────────────────────────────────
«                                                           
«q_3: ──────────────────────────────────────────────────────
«        ┌────────────┐                                     
«q_4: ───┤ Rz(1.0747) ├─────────────────────────────────────
«     ┌──┴────────────┴─┐  ┌──────────────┐                 
«q_5: ┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─────────────────
«     └─────────────────┘┌─┴──────────────┴┐┌─────────────┐ 
«q_6: ─────────■─────────┤ Ry(-8.1451e-06) ├┤ Rz(0.25427) ├─
«              │         └┬────────────────┤├─────────────┴┐
«q_7: ─────────■──────────┤ Ry(-0.0044055) ├┤ Rz(0.010242) ├
«              

In [16]:
#checking circuit

In [17]:
phase_y_front = [6.827165202923369e-06,-1.6337052388981617e-05, -1.9504648473842978e-05, -4.583505307611714e-05, 6.10354282870864e-05, 5.965270087646158e-06, 9.312744374460134e-06, -0.0043764639879769]
phase_z_front = [1.7168697590535538, 1.5283131502120553, 1.8467840590281954, 1.9183949883797635, 1.8180451683566035, 1.8290020607579571,1.7186918294701956 ,0.0005809279491065732 ]
phase_y_end = [1.7553477050418194e-05, -5.2173015630282704e-06, 2.7300161977647244e-05, 1.6108036965651842e-06,-8.147972934398958e-06, -8.65422271101483e-06, -8.145059343430974e-06, -0.0044055233224810164]
phase_z_end = [1.5640736434660867, 0.8907239659216719, 0.8895530769206249, -0.12591739710453853, 1.0747017329581952, -0.21554369415117478, 0.25426734596118483, 0.010241971123548377]
x_front = [True, False, True, False, True, False, True, False]

In [18]:
qubit_id = 5
circuit = QuantumCircuit(9)
apply_checking_circuit(circuit, [qubit_id], [8], side = 'front', phase_y = phase_y_front[qubit_id], phase_z = phase_z_front[qubit_id], x = x_front[qubit_id])
circuit += orign_circuit
apply_checking_circuit(circuit, [qubit_id], [8], side = 'end', phase_y = phase_y_end[qubit_id], phase_z = phase_z_end[qubit_id])

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_31273/2720963099.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  circuit += orign_circuit


In [19]:
circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼───────┤ Rz(1.7187) ├»
      ┌─────┴───┴──────┐ ├────────────────┤      │       └────────────┘»
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├──────┼─────────────────────»
      └─────┬───┬──────┘ └────────────────┘      │                     »
q_8: ───────┤ H ├────────────────────────────────■─────────────────────»
            └───┘                                                      »
«      ┌────────────────┐   ┌────────────┐                                    »
«q_0: ─┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├────────────────────────────────────»
«      └────────────────┘┌──┴────────────┴─┐┌─────────────┐                   »
«q_1: ─────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├───────────────────»
«              │         └─────────────────┘├─────────────┴┐ ┌─────────────┐  »
«q_2: ─────────■──────────────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├──»
«                                 │         └──────────────┘┌┴─────────────┴─┐»
«q_3: ────────────────────────────■────────────────■────────┤ Ry(1.6108e-06) ├»
«                                                  │        └────────────────┘»
«q_4: ─────────────────────────────────────────────■────────────────■─────────»
«     ┌─────────────────┐ ┌────────────────┐ ┌───────────┐          │         »
«q_5: ┤ Ry(-5.9653e-06) ├─┤ Ry(5.9653e-06) ├─┤ Rz(1.829) ├──────────■─────────»
«     └─────────────────┘ └────────────────┘ └───────────┘                    »
«q_6: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_7: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_8: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«                                                                             »
«q_0: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_1: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_2: ────────────────────────────────────────────────────────────────────────»
«      ┌──────────────┐                                                       »
«q_3: ─┤ Rz(-0.12592) ├───────────────────────────────────────────────────────»
«     ┌┴──────────────┴┐   ┌────────────┐                                     »
«q_4: ┤ Ry(-8.148e-06) ├───┤ Rz(1.0747) ├─────────────────────────────────────»
«     └────────────────┘┌──┴────────────┴─┐  ┌──────────────┐ ┌─────────────┐ »
«q_5: ────────■─────────┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─┤ Rz(0.21554) ├─»
«             │         └─────────────────┘┌─┴──────────────┴┐├─────────────┤ »
«q_6: ────────■──────────────────■─────────┤ Ry(-8.1451e-06) ├┤ R

In [21]:
pauli_list = read_from_file('HF_hamiltonian.txt')
pauli_commute = find_commute_groups(pauli_list)

In [24]:
#generate individual measurment circuits that changes the basis
meas_qcs = []
for i in range(0, len(pauli_commute)):
    temp_qc = MeasureCircuit(pauli_commute[i], num_qubits = 8,num_qargs = 9)
    meas_qcs.append(temp_qc)
    print(temp_qc)

YXXYYXXY
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_3: ┤ U(π/2,0,π/2) ├
     ├──────────────┤
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
XXXXYXXY
      ┌────────────┐ 
q_0: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_3: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
YXXYXXXX
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     

In [25]:
circuit_list = []
for meas in meas_qcs:
    temp_circuit = circuit.copy()
    temp_circuit += meas
    circuit_list.append(temp_circuit)

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_31273/1717817760.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  temp_circuit += meas


In [26]:
circuit_list[-2].draw()

┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼───────┤ Rz(1.7187) ├»
      ┌─────┴───┴──────┐ ├────────────────┤      │       └────────────┘»
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├──────┼─────────────────────»
      └─────┬───┬──────┘ └────────────────┘      │                     »
q_8: ───────┤ H ├────────────────────────────────■─────────────────────»
            └───┘                                                      »
«      ┌────────────────┐   ┌────────────┐                                    »
«q_0: ─┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├────────────────────────────────────»
«      └────────────────┘┌──┴────────────┴─┐┌─────────────┐                   »
«q_1: ─────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├───────────────────»
«              │         └─────────────────┘├─────────────┴┐ ┌─────────────┐  »
«q_2: ─────────■──────────────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├──»
«                                 │         └──────────────┘┌┴─────────────┴─┐»
«q_3: ────────────────────────────■────────────────■────────┤ Ry(1.6108e-06) ├»
«                                                  │        └────────────────┘»
«q_4: ─────────────────────────────────────────────■────────────────■─────────»
«     ┌─────────────────┐ ┌────────────────┐ ┌───────────┐          │         »
«q_5: ┤ Ry(-5.9653e-06) ├─┤ Ry(5.9653e-06) ├─┤ Rz(1.829) ├──────────■─────────»
«     └─────────────────┘ └────────────────┘ └───────────┘                    »
«q_6: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_7: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_8: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«                                                                             »
«q_0: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_1: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«q_2: ────────────────────────────────────────────────────────────────────────»
«      ┌──────────────┐                                                       »
«q_3: ─┤ Rz(-0.12592) ├───────────────────────────────────────────────────────»
«     ┌┴──────────────┴┐   ┌────────────┐                                     »
«q_4: ┤ Ry(-8.148e-06) ├───┤ Rz(1.0747) ├─────────────────────────────────────»
«     └────────────────┘┌──┴────────────┴─┐  ┌──────────────┐ ┌─────────────┐ »
«q_5: ────────■─────────┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─┤ Rz(0.21554) ├─»
«             │         └─────────────────┘┌─┴──────────────┴┐├─────────────┤ »
«q_6: ────────■──────────────────■─────────┤ Ry(-8.1451e-06) ├┤ R

In [27]:
# cuts = []
# for i in range(0, 1):
#     if i == 0 or i == qubits - 1:
#         cut = [(circuit.qubits[i], 5),(circuit.qubits[i], 6)]
#     else:
#         cut = [(circuit.qubits[i], 5),(circuit.qubits[i], 4)]
#     cuts += cut

In [28]:
cuts = [(circuit.qubits[5], 5),(circuit.qubits[5], 11)]

In [29]:
fragments_list = []
wire_path_map_list = []
for temp_qc in circuit_list:
    print(temp_qc)
    fragments, wire_path_map = circuit_cutter.cut_circuit(temp_qc, cuts)
    fragments_list.append(fragments)
    wire_path_map_list.append(wire_path_map)

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

...

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

            ┌───┐        ┌────────────────┐┌────────────┐              »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├──────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘      │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐              »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├──────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘              »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐               »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├───────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘ ┌────────────┐»
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────■───────┤ Rz(-1.829) ├»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │       ├────────────┤»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼─

In [30]:
print(wire_path_map_list[0])

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(8, 'q'), 0)),), Qubit(QuantumRegister(9, 'q'), 1): ((0, Qubit(QuantumRegister(8, 'q'), 6)),), Qubit(QuantumRegister(9, 'q'), 2): ((0, Qubit(QuantumRegister(8, 'q'), 4)),), Qubit(QuantumRegister(9, 'q'), 3): ((0, Qubit(QuantumRegister(8, 'q'), 2)),), Qubit(QuantumRegister(9, 'q'), 4): ((0, Qubit(QuantumRegister(8, 'q'), 5)),), Qubit(QuantumRegister(9, 'q'), 5): ((1, Qubit(QuantumRegister(3, 'q'), 0)), (0, Qubit(QuantumRegister(8, 'q'), 1)), (1, Qubit(QuantumRegister(3, 'q'), 1))), Qubit(QuantumRegister(9, 'q'), 6): ((0, Qubit(QuantumRegister(8, 'q'), 3)),), Qubit(QuantumRegister(9, 'q'), 7): ((0, Qubit(QuantumRegister(8, 'q'), 7)),), Qubit(QuantumRegister(9, 'q'), 8): ((1, Qubit(QuantumRegister(3, 'q'), 2)),)}


In [31]:
total_variants = ml.fragment_variants(wire_path_map_list[0])

In [32]:
total_variants

24

In [33]:
shots = 10000 * total_variants

In [34]:
fragments_list[0][0].draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘  │         │         »
q_6: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐                                   »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────────────────────────»
      └────────────────┘ └────────────────┘                                   »
«        ┌────────────┐  ┌──────────────┐                                     »
«q_0: ───┤ Rz(1.5641) ├──┤ U(π/2,0,π/2) ├─────────────────────────────────────»
«        └────────────┘  └──────────────┘                                     »
«q_1: ──────────────────────────────────────────────────────────────────────■─»
«                                        ┌────────────────┐┌──────────────┐ │ »
«q_2: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├┤ Rz(-0.12592) ├─┼─»
«              │                │        └────────────────┘└──────────────┘ │ »
«q_3: ─────────┼────────────────┼───────────────────────────────────────────┼─»
«              │                │         ┌──────────────┐ ┌─────────────┐  │ »
«q_4: ─────────■────────────────┼─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├──┼─»
«                               │         └──────────────┘ └─────────────┘  │ »
«q_5: ──────────────────────────■───────────────────────────────────────────■─»
«     ┌─────────────────┐┌─────────────┐   ┌────────────┐                     »
«q_6: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├───┤ U(π/2,0,π) ├─────────────────────»
«     └─────────────────┘└─────────────┘   └────────────┘                     »
«q_7: ────────────────────────────────────────────────────────────────────────»
«                                                                             »
«                                                                             »
«q_0: ────────────────────────────────────────────────────────────────────────»
«                       ┌─────────────────┐┌──────────────┐                   »
«q_1: ────────■─────────┤ Ry(-8.6542e-06) ├┤ Rz(-0.21554) ├───────────────────»
«             │         └─┬──────────────┬┘└──────────────┘                   »
«q_2: ────────┼───────────┤ U(π/2,0,π/2) ├────────────────────────────────────»
«             │           └──────────────┘                 ┌─────────────────┐»
«q_3: ────────■───────────────────────────────────■────────┤ Ry(-8.1451e-06) ├»
«       ┌────────────┐                            │        └─────────────────┘»
«q_4: ──┤ U(π/2,0,π) ├────────────────────────────┼───────────────────────────»
«     ┌─┴────────────┴─┐   ┌────────────┐         │          ┌──────────────┐ »
«q_5: ┤ Ry(-8.148e-06) ├───┤ Rz(1.0747) ├─────────┼──────────┤ U(π/2,0,π/2) ├─»
«     └────────────────┘   └────────────┘         │          └──────────────┘ »
«q_6: ────────────────────────────────────────────┼───────────────────────────»
«                                                 │         ┌────────────────┐»
«q_7: ────────────────────────────────────────────■─────────┤ Ry(-0.0044055) ├»
«           

In [35]:
fragment_cuts_list = []
for index in range(0, len(fragments_list)):
    for idx, fragment in enumerate(fragments_list[index]):
        print(f"fragment {idx}:")
        print(fragment)
        print()
    fragment_cuts = ml.fragment_cuts(wire_path_map_list[index])
    fragment_cuts_list.append(fragment_cuts)


fragment 0:
            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────

In [36]:
print(fragment_cuts_list[-1])

[{'prep': 1, 'meas': 1}, {'prep': 1, 'meas': 1}]


In [37]:
wire_path_map

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(8, 'q'), 0)),),
 Qubit(QuantumRegister(9, 'q'), 1): ((0, Qubit(QuantumRegister(8, 'q'), 6)),),
 Qubit(QuantumRegister(9, 'q'), 2): ((0, Qubit(QuantumRegister(8, 'q'), 4)),),
 Qubit(QuantumRegister(9, 'q'), 3): ((0, Qubit(QuantumRegister(8, 'q'), 2)),),
 Qubit(QuantumRegister(9, 'q'), 4): ((0, Qubit(QuantumRegister(8, 'q'), 5)),),
 Qubit(QuantumRegister(9, 'q'), 5): ((1, Qubit(QuantumRegister(3, 'q'), 0)),
  (0, Qubit(QuantumRegister(8, 'q'), 1)),
  (1, Qubit(QuantumRegister(3, 'q'), 1))),
 Qubit(QuantumRegister(9, 'q'), 6): ((0, Qubit(QuantumRegister(8, 'q'), 3)),),
 Qubit(QuantumRegister(9, 'q'), 7): ((0, Qubit(QuantumRegister(8, 'q'), 7)),),
 Qubit(QuantumRegister(9, 'q'), 8): ((1, Qubit(QuantumRegister(3, 'q'), 2)),)}

In [38]:
num_fragments = len(fragments)
num_fragments

2

In [39]:
num_tomo_circuits = len(meas_qcs)
num_tomo_circuits

76

In [40]:
fragments[0].draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘ │ └────────────────┘»
q_1: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
     ┌┴────────────────┤   ├───────────┴┐                 │                   »
q_2: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_3: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤       ┌┴────────────────┤├────────────┤ │                   »
q_4: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼─────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘ │         │         »
q_5: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼─────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘  │         │         »
q_6: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐                                   »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────────────────────────»
      └────────────────┘ └────────────────┘                                   »
«        ┌────────────┐   ┌────────────┐                                     »
«q_0: ───┤ Rz(1.5641) ├───┤ U(π/2,0,π) ├─────────────────────────────────────»
«        └────────────┘   └────────────┘                                     »
«q_1: ─────────────────────────────────────────────────────────────────────■─»
«                                       ┌────────────────┐┌──────────────┐ │ »
«q_2: ─────────■────────────────■───────┤ Ry(1.6108e-06) ├┤ Rz(-0.12592) ├─┼─»
«              │                │       └────────────────┘└──────────────┘ │ »
«q_3: ─────────┼────────────────┼──────────────────────────────────────────┼─»
«              │                │        ┌──────────────┐ ┌─────────────┐  │ »
«q_4: ─────────■────────────────┼────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├──┼─»
«                               │        └──────────────┘ └─────────────┘  │ »
«q_5: ──────────────────────────■──────────────────────────────────────────■─»
«     ┌─────────────────┐┌─────────────┐                                     »
«q_6: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘└─────────────┘                                     »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                                             »
«q_0: ────────────────────────────────────────────────────────────────────────»
«                       ┌─────────────────┐┌──────────────┐                   »
«q_1: ────────■─────────┤ Ry(-8.6542e-06) ├┤ Rz(-0.21554) ├───────────────────»
«             │         └─────────────────┘└──────────────┘                   »
«q_2: ────────┼───────────────────────────────────────────────────────────────»
«             │                                            ┌─────────────────┐»
«q_3: ────────■───────────────────────────────────■────────┤ Ry(-8.1451e-06) ├»
«                                                 │        └─────────────────┘»
«q_4: ────────────────────────────────────────────┼───────────────────────────»
«     ┌────────────────┐   ┌────────────┐         │                           »
«q_5: ┤ Ry(-8.148e-06) ├───┤ Rz(1.0747) ├─────────┼───────────────────────────»
«     └────────────────┘   └────────────┘         │                           »
«q_6: ────────────────────────────────────────────┼───────────────────────────»
«                                                 │         ┌────────────────┐»
«q_7: ────────────────────────────────────────────■─────────┤ Ry(-0.0044055) ├»
«                            

In [41]:
fragments[1].draw()

┌────────────────┐  ┌───────────┐      ┌────────────┐┌─────────────────┐»
q_0: ┤ Ry(5.9653e-06) ├──┤ Rz(1.829) ├────■─┤ Rz(-1.829) ├┤ Ry(-5.9653e-06) ├»
     └┬─────────────┬─┘┌─┴───────────┴──┐ │ └────────────┘├─────────────────┤»
q_1: ─┤ Rz(0.21554) ├──┤ Ry(8.6542e-06) ├─┼───────■───────┤ Ry(-8.6542e-06) ├»
      └────┬───┬────┘  └────────────────┘ │       │       └──────┬───┬──────┘»
q_2: ──────┤ H ├──────────────────────────■───────■──────────────┤ H ├───────»
           └───┘                                                 └───┘       »
«                     
«q_0: ────────────────
«     ┌──────────────┐
«q_1: ┤ Rz(-0.21554) ├
«     └──────────────┘
«q_2: ────────────────
«

In [42]:
hardware_index = 0

In [43]:
print(shots)

240000


In [44]:
tomography_circuits = []
for idx in range(0, len(fragments_list)):
    fragments = fragments_list[idx]
    wire_path_map = wire_path_map_list[idx]
    temp_frag_circuits = [0] * len(fragments)
    for i in range(0, len(fragments)):
        if i == hardware_index:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
        else:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
    tomography_circuits.append(temp_frag_circuits)

In [45]:
#contains 34 basis
len(tomography_circuits)

76

In [46]:
#contains two fragments
len(tomography_circuits[0])

2

In [47]:
len(tomography_circuits[0][1])

1

In [48]:
#tomography circuits
len(tomography_circuits[0][1][0])

12

In [49]:
multi_exp_circuits = [[],[]]
for i in range(0, len(tomography_circuits)):
    #for each basis collect the three fragments:
    for j in range(0, num_fragments):
        fragment_circ = tomography_circuits[i][j][0]
        multi_exp_circuits[j] += fragment_circ

In [50]:
#[9,8,11,14,13,12,10,7]
#06425137
#[9,12,14,10,11,13,8,7]

In [51]:
multi_exp_circuits[hardware_index][-200].draw()

░        ┌───┐        ┌────────────────┐»
   q_0: ────────────────────░────────┤ X ├────────┤ Ry(6.8272e-06) ├»
        ┌─────────────────┐ ░  ┌─────┴───┴──────┐ └─┬───────────┬──┘»
   q_1: ┤ U3(-1.9106,π,0) ├─░──┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├───»
        └─────────────────┘ ░ ┌┴────────────────┤   ├───────────┴┐  »
   q_2: ────────────────────░─┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──»
                            ░ └──────┬───┬──────┘ ┌─┴────────────┴─┐»
   q_3: ────────────────────░────────┤ X ├────────┤ Ry(9.3127e-06) ├»
                            ░        ├───┤       ┌┴────────────────┤»
   q_4: ────────────────────░────────┤ X ├───────┤ Ry(-1.9505e-05) ├»
                            ░        ├───┤       └┬────────────────┤»
   q_5: ────────────────────░────────┤ X ├────────┤ Ry(6.1035e-05) ├»
                            ░ ┌──────┴───┴──────┐ └─┬────────────┬─┘»
   q_6: ────────────────────░─┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──»
                            ░ └┬────────────────┤ ┌─┴────────────┴─┐»
   q_7: ────────────────────░──┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├»
                            ░  └────────────────┘ └────────────────┘»
c118_0: ════════════════════════════════════════════════════════════»
                                                                    »
c118_1: ════════════════════════════════════════════════════════════»
                                                                    »
c118_2: ════════════════════════════════════════════════════════════»
                                                                    »
c118_3: ════════════════════════════════════════════════════════════»
                                                                    »
c118_4: ════════════════════════════════════════════════════════════»
                                                                    »
c118_5: ════════════════════════════════════════════════════════════»
                                                                    »
c118_6: ════════════════════════════════════════════════════════════»
                                                                    »
c118_7: ════════════════════════════════════════════════════════════»
                                                                    »
«        ┌────────────┐   ┌────────────────┐   ┌────────────┐   ┌────────────┐»
«   q_0: ┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├───┤ U(π/2,0,π) ├»
«        └────────────┘ │ └────────────────┘   └────────────┘   └────────────┘»
«   q_1: ───────────────┼─────────────────────────────────────────────────────»
«                       │                                                     »
«   q_2: ───────────────┼────────────────────────────■────────────────■───────»
«        ┌────────────┐ │                            │                │       »
«   q_3: ┤ Rz(1.7187) ├─┼────────────────────────────┼────────────────┼───────»
«        ├────────────┤ │                            │                │       »
«   q_4: ┤ Rz(1.8468) ├─┼─────────■──────────────────■────────────────┼───────»
«        ├───────────┬┘ │         │                                   │       »
«   q_5: ┤ Rz(1.818) ├──┼─────────┼───────────────────────────────────■───────»
«        └───────────┘  │         │         ┌─────────────────┐┌─────────────┐»
«   q_6: ───────────────■─────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├»
«                                           └─────────────────┘└─────────────┘»
«   q_7: ─────────────────────────────────────────────────────────────────────»
«                                                                             »
«c118_0: ═════════════════════════════════════════════════════════════════════»
«                                                                             »
«c118_1: ═════════════════════════════════════════════════════════════════════»
«                                                                             »
«c118_2: ═════════════════════════════

In [50]:
len(multi_exp_circuits[0])

408

In [52]:
frag_datas = [0] * num_fragments
for i in range(0, num_fragments):
    if i == hardware_index:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = [9,12,14,10,11,13,8,7],
                                     backend = device, shots = shots // total_variants, 
                                     optimization_level = 3, monitor_jobs = True)
    else:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = None,
                                     backend = simulation_backend, shots = shots // total_variants,
                                     optimization_level = 3, monitor_jobs = True, noise_model = None)
       

jobset_id:  0004c8d251c04df18214621557bf4399-1670516847584933
job_id:  0c7fa6e6-74cb-4787-bb6e-016ae3f0a503
Job Status: job has successfully run


In [ ]:
frag_datas[1]

In [117]:
# from qiskit.providers.ibmq.managed import IBMQJobManager
# job_manager = IBMQJobManager()

In [118]:
# job_set = job_manager.retrieve_job_set(job_set_id='973c2fdceaf547389a770d19aad463d8-1669966038684177', provider=provider)

In [119]:
# managed_results = job_set.results()

In [120]:
# frag_datas1_copy = frag_datas[1].copy()

In [53]:
frag_datas[0] = [frag_datas[0][0].combine_results()]

In [54]:
# frag_datas[0] = run_circuits(multi_exp_circuits[0], initial_layout = None,
#                              backend = simulation_backend, shots = shots // total_variants,
#                              optimization_level = 3, monitor_jobs = True, noise_model = None)

In [55]:
frag_datas[0][0].results[0].header.name

"(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z'))"

In [56]:
num_tomo_circuits

76

In [57]:
test = [[], []]

In [58]:
results_list = [[], []]
counts_list = [[], []] 
for i in range(0, num_fragments): 
    for j in range(0, num_tomo_circuits):
        start_idx = j * 12
        end_idx = (j + 1) * 12
        results_list[i].append(frag_datas[i][0].results[start_idx : end_idx])
        counts_list[i].append(frag_datas[i][0].get_counts()[start_idx : end_idx])


In [60]:
from mlrecon_methods import organize_tomography_data_from_list
organized_data = []
for i in range(0, num_tomo_circuits):
    frag_data = []
    frag_targets = ml.identify_frag_targets(wire_path_map_list[i])
    for j in range(0, num_fragments):
        frag_data.append(organize_tomography_data_from_list(results_list[j][i], counts_list[j][i],
                                              frag_targets[j].get("prep"),
                                              frag_targets[j].get("meas"),
                                              prep_basis = "SIC", extra_qc = []))
    organized_data.append(frag_data)

(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('Z',) [1] [1]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('X',) [1] [1]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('Y',) [1] [1]
(('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S1

(('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S2',) ('Y',) [1] [1]
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S3',) ('Z',) [1] [1]
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S3',) ('X',) [1] [1]
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S3

(('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S1',) ('X',) [1] [1]
(('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S1', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S1',) ('Y',) [1] [1]
(('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S2',) ('Z',) [1] [1]
(('S0', 'S2', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S2

(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S3',) ('Z',) [1] [1]
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'X', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S3',) ('X',) [1] [1]
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S3', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Y', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S3',) ('Y',) [1] [1]
(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S0') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S0'), ('Z', 'Z'

In [61]:
for final_bits, fixed_bit_data in frag_data[0].items():
    prep_meas_states, state_counts = zip(*fixed_bit_data.items())
    prep_labels, meas_labels = zip(*prep_meas_states)
    prep_qubit_num = len(prep_labels[0])
    meas_qubit_num = len(meas_labels[0])
    print(prep_qubit_num)

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


In [62]:
recombined_lists = []
filtered_recombined_lists = []
norm_filtered_lists = []
for i in range(0, num_tomo_circuits):
    direct_models = ml.direct_fragment_model(organized_data[i])
    likely_models = ml.maximum_likelihood_model(direct_models)

    direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map_list[i])
    likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map_list[i])
    recombined_lists.append(likely_recombined_dist)
    filtered_recombined_lists.append(filter_results(likely_recombined_dist, [0]))
    norm_filtered_lists.append(norm_dict(filter_results(likely_recombined_dist, [0])))

{'0000000': {(('S0',), ('Zp',)): 80, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 22, (('S0',), ('Xm',)): 17, (('S0',), ('Yp',)): 33, (('S0',), ('Ym',)): 32, (('S1',), ('Zp',)): 27, (('S1',), ('Zm',)): 53, (('S1',), ('Xp',)): 35, (('S1',), ('Xm',)): 45, (('S1',), ('Yp',)): 56, (('S1',), ('Ym',)): 8, (('S2',), ('Zp',)): 18, (('S2',), ('Zm',)): 53, (('S2',), ('Xp',)): 58, (('S2',), ('Xm',)): 7, (('S2',), ('Yp',)): 25, (('S2',), ('Ym',)): 43, (('S3',), ('Zp',)): 31, (('S3',), ('Zm',)): 55, (('S3',), ('Xp',)): 16, (('S3',), ('Xm',)): 58, (('S3',), ('Yp',)): 22, (('S3',), ('Ym',)): 56}, '0000001': {(('S0',), ('Zp',)): 64, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 36, (('S0',), ('Xm',)): 46, (('S0',), ('Yp',)): 31, (('S0',), ('Ym',)): 31, (('S1',), ('Zp',)): 22, (('S1',), ('Zm',)): 56, (('S1',), ('Xp',)): 26, (('S1',), ('Xm',)): 43, (('S1',), ('Yp',)): 67, (('S1',), ('Ym',)): 11, (('S2',), ('Zp',)): 23, (('S2',), ('Zm',)): 62, (('S2',), ('Xp',)): 60, (('S2',), ('Xm',)): 9, (('S2',), ('Yp',)):

{'01': {(('S0',), ('Zp',)): 5063, (('S0',), ('Xm',)): 2483, (('S0',), ('Xp',)): 2451, (('S0',), ('Ym',)): 2481, (('S0',), ('Yp',)): 2600, (('S1',), ('Zp',)): 1674, (('S1',), ('Xp',)): 839, (('S1',), ('Xm',)): 860, (('S1',), ('Yp',)): 878, (('S1',), ('Ym',)): 839, (('S2',), ('Zp',)): 1664, (('S2',), ('Xm',)): 815, (('S2',), ('Xp',)): 779, (('S2',), ('Yp',)): 794, (('S2',), ('Ym',)): 833, (('S3',), ('Zp',)): 1669, (('S3',), ('Xm',)): 868, (('S3',), ('Xp',)): 772, (('S3',), ('Ym',)): 850, (('S3',), ('Yp',)): 829, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '00': {(('S0',), ('Zp',)): 4937, (('S0',), ('Xm',)): 2502, (('S0',), ('Xp',)): 2564, (('S0',), ('Ym',)): 2440, (('S0',), ('Yp',)): 2479, (('S1',), ('Zp',)): 1602, (('S1',), ('Xp',)): 775, (('S1',), ('Xm',)): 776, (('S1',), ('Yp',)): 813, (('S1',), ('Ym',)): 873, (('S2',), ('Zp',)): 1689, (('S2',), ('Xm',)): 851, (('S2',), ('Xp',)): 843, (('S2',), ('Ym',)): 855, (('S2',), ('Yp',)): 887, ((

{'01': {(('S0',), ('Zp',)): 4966, (('S0',), ('Xm',)): 2498, (('S0',), ('Xp',)): 2533, (('S0',), ('Yp',)): 2491, (('S0',), ('Ym',)): 2538, (('S1',), ('Zp',)): 1712, (('S1',), ('Xp',)): 811, (('S1',), ('Xm',)): 822, (('S1',), ('Yp',)): 854, (('S1',), ('Ym',)): 825, (('S2',), ('Zp',)): 1610, (('S2',), ('Xm',)): 837, (('S2',), ('Xp',)): 830, (('S2',), ('Ym',)): 839, (('S2',), ('Yp',)): 876, (('S3',), ('Zp',)): 1664, (('S3',), ('Xp',)): 819, (('S3',), ('Xm',)): 840, (('S3',), ('Yp',)): 829, (('S3',), ('Ym',)): 843, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '00': {(('S0',), ('Zp',)): 5034, (('S0',), ('Xm',)): 2455, (('S0',), ('Xp',)): 2514, (('S0',), ('Ym',)): 2540, (('S0',), ('Yp',)): 2431, (('S1',), ('Zp',)): 1663, (('S1',), ('Xp',)): 849, (('S1',), ('Xm',)): 803, (('S1',), ('Ym',)): 805, (('S1',), ('Yp',)): 841, (('S2',), ('Zp',)): 1640, (('S2',), ('Xm',)): 931, (('S2',), ('Xp',)): 769, (('S2',), ('Ym',)): 891, (('S2',), ('Yp',)): 805, ((

{'01': {(('S0',), ('Zp',)): 5036, (('S0',), ('Xm',)): 2437, (('S0',), ('Xp',)): 2550, (('S0',), ('Ym',)): 2482, (('S0',), ('Yp',)): 2446, (('S1',), ('Zp',)): 1688, (('S1',), ('Xm',)): 821, (('S1',), ('Xp',)): 834, (('S1',), ('Yp',)): 845, (('S1',), ('Ym',)): 827, (('S2',), ('Zp',)): 1661, (('S2',), ('Xm',)): 832, (('S2',), ('Xp',)): 806, (('S2',), ('Ym',)): 803, (('S2',), ('Yp',)): 843, (('S3',), ('Zp',)): 1680, (('S3',), ('Xm',)): 823, (('S3',), ('Xp',)): 860, (('S3',), ('Ym',)): 829, (('S3',), ('Yp',)): 818, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '00': {(('S0',), ('Zp',)): 4964, (('S0',), ('Xp',)): 2454, (('S0',), ('Xm',)): 2559, (('S0',), ('Yp',)): 2552, (('S0',), ('Ym',)): 2520, (('S1',), ('Zp',)): 1627, (('S1',), ('Xp',)): 798, (('S1',), ('Xm',)): 837, (('S1',), ('Yp',)): 803, (('S1',), ('Ym',)): 831, (('S2',), ('Zp',)): 1659, (('S2',), ('Xm',)): 879, (('S2',), ('Xp',)): 857, (('S2',), ('Ym',)): 806, (('S2',), ('Yp',)): 859, ((

{'0000000': {(('S0',), ('Zp',)): 9, (('S0',), ('Xp',)): 10, (('S0',), ('Xm',)): 3, (('S0',), ('Yp',)): 2, (('S0',), ('Ym',)): 8, (('S1',), ('Zp',)): 1, (('S1',), ('Zm',)): 5, (('S1',), ('Xp',)): 4, (('S1',), ('Xm',)): 7, (('S1',), ('Yp',)): 16, (('S2',), ('Zp',)): 4, (('S2',), ('Zm',)): 6, (('S2',), ('Xp',)): 8, (('S2',), ('Ym',)): 5, (('S3',), ('Zp',)): 4, (('S3',), ('Zm',)): 7, (('S3',), ('Xp',)): 2, (('S3',), ('Xm',)): 8, (('S3',), ('Ym',)): 9, (('S0',), ('Zm',)): 0, (('S1',), ('Ym',)): 0, (('S2',), ('Xm',)): 0, (('S2',), ('Yp',)): 0, (('S3',), ('Yp',)): 0}, '0000001': {(('S0',), ('Zp',)): 197, (('S0',), ('Zm',)): 3, (('S0',), ('Xp',)): 113, (('S0',), ('Xm',)): 100, (('S0',), ('Yp',)): 103, (('S0',), ('Ym',)): 107, (('S1',), ('Zp',)): 74, (('S1',), ('Zm',)): 142, (('S1',), ('Xp',)): 102, (('S1',), ('Xm',)): 134, (('S1',), ('Yp',)): 207, (('S1',), ('Ym',)): 14, (('S2',), ('Zp',)): 65, (('S2',), ('Zm',)): 133, (('S2',), ('Xp',)): 175, (('S2',), ('Xm',)): 27, (('S2',), ('Yp',)): 102, (

...

{'0000000': {(('S0',), ('Zp',)): 92, (('S0',), ('Zm',)): 3, (('S0',), ('Xp',)): 43, (('S0',), ('Xm',)): 47, (('S0',), ('Yp',)): 37, (('S0',), ('Ym',)): 55, (('S1',), ('Zp',)): 36, (('S1',), ('Zm',)): 56, (('S1',), ('Xp',)): 41, (('S1',), ('Xm',)): 52, (('S1',), ('Yp',)): 89, (('S1',), ('Ym',)): 8, (('S2',), ('Zp',)): 38, (('S2',), ('Zm',)): 68, (('S2',), ('Xp',)): 86, (('S2',), ('Xm',)): 11, (('S2',), ('Yp',)): 33, (('S2',), ('Ym',)): 53, (('S3',), ('Zp',)): 32, (('S3',), ('Zm',)): 73, (('S3',), ('Xp',)): 21, (('S3',), ('Xm',)): 91, (('S3',), ('Yp',)): 32, (('S3',), ('Ym',)): 72}, '0000001': {(('S0',), ('Zp',)): 70, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 49, (('S0',), ('Xm',)): 47, (('S0',), ('Yp',)): 41, (('S0',), ('Ym',)): 54, (('S1',), ('Zp',)): 31, (('S1',), ('Zm',)): 52, (('S1',), ('Xp',)): 41, (('S1',), ('Xm',)): 59, (('S1',), ('Yp',)): 93, (('S1',), ('Ym',)): 7, (('S2',), ('Zp',)): 33, (('S2',), ('Zm',)): 68, (('S2',), ('Xp',)): 97, (('S2',), ('Xm',)): 17, (('S2',), ('Yp',))

{'0000000': {(('S0',), ('Zp',)): 96, (('S0',), ('Xp',)): 50, (('S0',), ('Xm',)): 39, (('S0',), ('Yp',)): 31, (('S0',), ('Ym',)): 37, (('S1',), ('Zp',)): 37, (('S1',), ('Zm',)): 67, (('S1',), ('Xp',)): 44, (('S1',), ('Xm',)): 53, (('S1',), ('Yp',)): 85, (('S1',), ('Ym',)): 11, (('S2',), ('Zp',)): 24, (('S2',), ('Zm',)): 73, (('S2',), ('Xp',)): 70, (('S2',), ('Xm',)): 11, (('S2',), ('Yp',)): 33, (('S2',), ('Ym',)): 48, (('S3',), ('Zp',)): 40, (('S3',), ('Zm',)): 74, (('S3',), ('Xp',)): 23, (('S3',), ('Xm',)): 86, (('S3',), ('Yp',)): 23, (('S3',), ('Ym',)): 71, (('S0',), ('Zm',)): 0}, '0000001': {(('S0',), ('Zp',)): 78, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 33, (('S0',), ('Xm',)): 30, (('S0',), ('Yp',)): 33, (('S0',), ('Ym',)): 35, (('S1',), ('Zp',)): 31, (('S1',), ('Zm',)): 60, (('S1',), ('Xp',)): 28, (('S1',), ('Xm',)): 43, (('S1',), ('Yp',)): 70, (('S1',), ('Ym',)): 15, (('S2',), ('Zp',)): 20, (('S2',), ('Zm',)): 50, (('S2',), ('Xp',)): 68, (('S2',), ('Xm',)): 10, (('S2',), ('Yp',

{'00': {(('S0',), ('Zp',)): 4995, (('S0',), ('Xp',)): 2565, (('S0',), ('Xm',)): 2475, (('S0',), ('Ym',)): 2526, (('S0',), ('Yp',)): 2476, (('S1',), ('Zp',)): 1659, (('S1',), ('Xm',)): 826, (('S1',), ('Xp',)): 808, (('S1',), ('Yp',)): 846, (('S1',), ('Ym',)): 821, (('S2',), ('Zp',)): 1688, (('S2',), ('Xp',)): 822, (('S2',), ('Xm',)): 866, (('S2',), ('Ym',)): 881, (('S2',), ('Yp',)): 823, (('S3',), ('Zp',)): 1715, (('S3',), ('Xm',)): 852, (('S3',), ('Xp',)): 816, (('S3',), ('Yp',)): 836, (('S3',), ('Ym',)): 778, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 5005, (('S0',), ('Xm',)): 2484, (('S0',), ('Xp',)): 2476, (('S0',), ('Ym',)): 2503, (('S0',), ('Yp',)): 2495, (('S1',), ('Zp',)): 1601, (('S1',), ('Xm',)): 822, (('S1',), ('Xp',)): 793, (('S1',), ('Yp',)): 843, (('S1',), ('Ym',)): 826, (('S2',), ('Zp',)): 1675, (('S2',), ('Xp',)): 857, (('S2',), ('Xm',)): 841, (('S2',), ('Ym',)): 852, (('S2',), ('Yp',)): 806, ((

{'0000001': {(('S0',), ('Zp',)): 3, (('S0',), ('Xp',)): 1, (('S0',), ('Yp',)): 1, (('S0',), ('Ym',)): 2, (('S1',), ('Zp',)): 1, (('S1',), ('Zm',)): 2, (('S1',), ('Xm',)): 1, (('S1',), ('Ym',)): 2, (('S2',), ('Zp',)): 2, (('S2',), ('Zm',)): 2, (('S2',), ('Xp',)): 1, (('S2',), ('Xm',)): 1, (('S2',), ('Yp',)): 1, (('S2',), ('Ym',)): 1, (('S3',), ('Xp',)): 2, (('S3',), ('Xm',)): 1, (('S3',), ('Yp',)): 2, (('S3',), ('Ym',)): 2, (('S0',), ('Zm',)): 0, (('S0',), ('Xm',)): 0, (('S1',), ('Xp',)): 0, (('S1',), ('Yp',)): 0, (('S3',), ('Zp',)): 0, (('S3',), ('Zm',)): 0}, '0001000': {(('S0',), ('Zp',)): 4, (('S0',), ('Zm',)): 1, (('S0',), ('Ym',)): 2, (('S1',), ('Zm',)): 4, (('S1',), ('Xp',)): 1, (('S1',), ('Xm',)): 1, (('S1',), ('Yp',)): 1, (('S1',), ('Ym',)): 2, (('S2',), ('Zp',)): 2, (('S2',), ('Zm',)): 1, (('S2',), ('Xp',)): 1, (('S2',), ('Yp',)): 2, (('S3',), ('Zp',)): 1, (('S3',), ('Zm',)): 1, (('S3',), ('Xp',)): 2, (('S3',), ('Xm',)): 2, (('S0',), ('Xp',)): 0, (('S0',), ('Xm',)): 0, (('S0',)

{'00': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xm',)): 4996, (('S0',), ('Xp',)): 5004, (('S0',), ('Yp',)): 4916, (('S0',), ('Ym',)): 5084, (('S1',), ('Zp',)): 3353, (('S1',), ('Xp',)): 1649, (('S1',), ('Xm',)): 1636, (('S1',), ('Ym',)): 1660, (('S1',), ('Yp',)): 1725, (('S2',), ('Zp',)): 3345, (('S2',), ('Xm',)): 1632, (('S2',), ('Xp',)): 1617, (('S2',), ('Ym',)): 1662, (('S2',), ('Yp',)): 1660, (('S3',), ('Zp',)): 3311, (('S3',), ('Xp',)): 1595, (('S3',), ('Xm',)): 1660, (('S3',), ('Yp',)): 1688, (('S3',), ('Ym',)): 1698, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '11': {(('S1',), ('Zp',)): 6647, (('S1',), ('Xp',)): 3336, (('S1',), ('Xm',)): 3379, (('S1',), ('Yp',)): 3393, (('S1',), ('Ym',)): 3222, (('S2',), ('Zp',)): 6655, (('S2',), ('Xp',)): 3360, (('S2',), ('Xm',)): 3391, (('S2',), ('Ym',)): 3298, (('S2',), ('Yp',)): 3380, (('S3',), ('Zp',)): 6689, (('S3',), ('Xm',)): 3381, (('S3',), ('Xp',)): 3364, (('S3',), ('Yp',)): 3297, (('S3',

In [63]:
# direct_models = ml.direct_fragment_model(frag_data)
# likely_models = ml.maximum_likelihood_model(direct_models)

# direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map)
# likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map)

In [64]:
from utils.utils import filter_results

In [65]:
filter_direct_recombined = filter_results(direct_recombined_dist, [0])

In [66]:

filter_likely_recombined = filter_results(likely_recombined_dist, [0])

In [67]:
norm_filter_dist = norm_dict(filter_likely_recombined)

In [68]:
final_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        final_expect_val += coeff * evaluation(norm_filtered_lists[i], shots = total_counts(norm_filtered_lists[i]), Pauli = Pauli_tuple[0])  

In [69]:
final_expect_val

(-27.776669962330732+0j)

In [70]:
import json
with open('HF_auckland_check5.json', 'w') as f:
    json.dump(norm_filtered_lists, f)

In [71]:
mit = mthree.M3Mitigation(device)
mit.cals_from_file(cals_file = 'mit_data_9_8_14_11_13_12_10_7')

In [72]:
def update_dict(quasis, total_shots = None):
    for key in quasis.keys():
        quasis[key] = quasis[key]*total_shots

In [73]:
mit_lists = []
for i in range(0, len(pauli_commute)):
    total_shots = total_counts(norm_filtered_lists[i])
    quasis = mit.apply_correction(norm_filtered_lists[i], [9,8,14,11,13,12,10,7])
    update_dict(quasis, total_shots = total_shots)
    mit_lists.append(quasis)
miti_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        miti_expect_val += coeff * evaluation(mit_lists[i], shots = total_counts(mit_lists[i]), Pauli = Pauli_tuple[0]) 
miti_expect_val

(-27.91657791133712+0j)

In [76]:
with open('HF_auckland_check5_mit.json', 'w') as f:
    json.dump(mit_lists, f)